# Table of Contents
 <p><div class="lev1 toc-item"><a href="#Class-1-Neural-Network-Experiments-for-MORPHE-MU" data-toc-modified-id="Class-1-Neural-Network-Experiments-for-MORPHE-MU-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Class 1 Neural Network Experiments for MORPHE-MU</a></div><div class="lev2 toc-item"><a href="#1.-Setup-task" data-toc-modified-id="1.-Setup-task-11"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>1. Setup task</a></div><div class="lev2 toc-item"><a href="#2.-Try-using-MLP-in-TensorFlow" data-toc-modified-id="2.-Try-using-MLP-in-TensorFlow-12"><span class="toc-item-num">1.2&nbsp;&nbsp;</span>2. Try using MLP in TensorFlow</a></div><div class="lev2 toc-item"><a href="#3.-Build-Class-1-Neural-Network-and-experiment" data-toc-modified-id="3.-Build-Class-1-Neural-Network-and-experiment-13"><span class="toc-item-num">1.3&nbsp;&nbsp;</span>3. Build Class 1 Neural Network and experiment</a></div><div class="lev3 toc-item"><a href="#Test-creating-index-mapping" data-toc-modified-id="Test-creating-index-mapping-131"><span class="toc-item-num">1.3.1&nbsp;&nbsp;</span>Test creating index mapping</a></div><div class="lev3 toc-item"><a href="#Index-mapping-function" data-toc-modified-id="Index-mapping-function-132"><span class="toc-item-num">1.3.2&nbsp;&nbsp;</span>Index mapping function</a></div><div class="lev3 toc-item"><a href="#Test-statistics-of-index-mapping-function" data-toc-modified-id="Test-statistics-of-index-mapping-function-133"><span class="toc-item-num">1.3.3&nbsp;&nbsp;</span>Test statistics of index mapping function</a></div><div class="lev3 toc-item"><a href="#Utility-functions-for-neural-network" data-toc-modified-id="Utility-functions-for-neural-network-134"><span class="toc-item-num">1.3.4&nbsp;&nbsp;</span>Utility functions for neural network</a></div><div class="lev3 toc-item"><a href="#Class-1A-Neural-Network-implementation" data-toc-modified-id="Class-1A-Neural-Network-implementation-135"><span class="toc-item-num">1.3.5&nbsp;&nbsp;</span>Class 1A Neural Network implementation</a></div><div class="lev3 toc-item"><a href="#Trying-out-on-MNIST" data-toc-modified-id="Trying-out-on-MNIST-136"><span class="toc-item-num">1.3.6&nbsp;&nbsp;</span>Trying out on MNIST</a></div><div class="lev3 toc-item"><a href="#Class-1A-+-Gaussian-Selectrick-Implementation" data-toc-modified-id="Class-1A-+-Gaussian-Selectrick-Implementation-137"><span class="toc-item-num">1.3.7&nbsp;&nbsp;</span>Class 1A + Gaussian Selectrick Implementation</a></div><div class="lev3 toc-item"><a href="#Class-1A-+-Seltrick-on-MNIST-dataset" data-toc-modified-id="Class-1A-+-Seltrick-on-MNIST-dataset-138"><span class="toc-item-num">1.3.8&nbsp;&nbsp;</span>Class 1A + Seltrick on MNIST dataset</a></div><div class="lev4 toc-item"><a href="#Configurations" data-toc-modified-id="Configurations-1381"><span class="toc-item-num">1.3.8.1&nbsp;&nbsp;</span>Configurations</a></div><div class="lev4 toc-item"><a href="#Configuration-0" data-toc-modified-id="Configuration-0-1382"><span class="toc-item-num">1.3.8.2&nbsp;&nbsp;</span>Configuration 0</a></div><div class="lev4 toc-item"><a href="#Configuration-1" data-toc-modified-id="Configuration-1-1383"><span class="toc-item-num">1.3.8.3&nbsp;&nbsp;</span>Configuration 1</a></div><div class="lev3 toc-item"><a href="#Neural-network-configuration" data-toc-modified-id="Neural-network-configuration-139"><span class="toc-item-num">1.3.9&nbsp;&nbsp;</span>Neural network configuration</a></div><div class="lev3 toc-item"><a href="#Running-neural-network" data-toc-modified-id="Running-neural-network-1310"><span class="toc-item-num">1.3.10&nbsp;&nbsp;</span>Running neural network</a></div>

# Class 1 Neural Network Experiments for MORPHE-MU

In [2]:
%load_ext Cython

In [3]:
import faulthandler
import tensorflow as tf
import skimage.draw
import skimage.filters
import numpy as np
import random
import functools
import math
import sklearn
import sklearn.model_selection
import scipy
import bokeh.plotting as p
import bokeh.charts as c
import bokeh.layouts as bl
import tensorflow.contrib
import tensorflow.contrib.losses
from tensorflow.python.client import timeline
from IPython.display import Math

faulthandler.enable()

In [4]:
p.output_notebook()

Loading BokehJS ...

## 1. Setup task

We are going to create a set of geometric figures, and the task of the neural net is to correctly identify positions of the circles. Input is grayscale 2D image data, and the output is a 2D matrix with probabilities of a circle being in corresponding rectangular section of the input image.

In [5]:

def create_dataset(count, f, seed = 42):
    random.seed(seed)
    
    dataset = []
    
    for _ in range(count):
        dataset += [f()]
    
    return dataset

def create_canvas(element_count, size = (512,512), only_circles = False, use_ellipse = False, apply_gauss = False):
    canvas = np.zeros(size)
    circles = []
    if only_circles:
        figures = ['circle']
    elif use_ellipse:
        figures = ['circle', 'rectangle', 'ellipse']
    else:
        figures = ['circle', 'rectangle']
        
    for _ in range(element_count):
        figure = random.choice(figures)
        fill_color = random.random() * 0.8 + 0.2
        border_color = 1.0
        if figure == 'circle':
            radius = random.randint(5, min(size)//3)
            loc_x = random.randint(0, size[0])
            loc_y = random.randint(0, size[1])
            shape_perimeter = skimage.draw.circle_perimeter(loc_y, loc_x, radius, shape = size)
            shape_figure = skimage.draw.circle(loc_y, loc_x, radius, shape = size)
            
            circles += [(loc_x, loc_y, radius)]
        elif figure == 'rectangle':
            size_x = random.randint(5, min(size)//3)
            size_y = random.randint(5, min(size)//3)
            loc_x = random.randint(0, size[0])
            loc_y = random.randint(0, size[1])
            vertices_row = [loc_y-size_y, loc_y-size_y, loc_y+size_y, loc_y+size_y]
            vertices_column = [loc_x-size_x, loc_x+size_x, loc_x+size_x, loc_x-size_x]
            
            shape_perimeter = skimage.draw.polygon_perimeter(vertices_row, vertices_column, shape = size)
            shape_figure = skimage.draw.polygon(vertices_row, vertices_column, shape = size)
        elif figure == 'triangle':
            shape_figure = []
            shape_perimeter = []
            pass
        elif figure == 'ellipse':
            shape_figure = []
            shape_perimeter = []
            pass
        else:
            raise RuntimeError
            
        canvas[shape_figure] = fill_color
        canvas[shape_perimeter] = border_color
    
    if apply_gauss:
        canvas = skimage.filters.gaussian(canvas, sigma=0.5)
            
    return (canvas, circles)
    


Build a dataset of 500 images.

In [6]:
dataset_image_shape = (64,64)

dataset_creator_f = functools.partial(create_canvas, 5, size = dataset_image_shape, only_circles = False, apply_gauss = True)
image_dataset = create_dataset(500, dataset_creator_f)

In [6]:
fig1_idx = 1

fig1 = p.figure(x_range=[0,1], y_range=[0,1])
fig1.image([image_dataset[fig1_idx][0]], 0, 0, 1, 1, palette='Magma256')
fig1_data = np.transpose(image_dataset[fig1_idx][1]) / dataset_image_shape[0]
fig1.cross(fig1_data[0], fig1_data[1], size=20, color='red', line_width=3.0, angle=math.pi/4)
for x,y,r in fig1_data.T:
    fig1.line([x, min(x+r, dataset_image_shape[0])], [y, y], color='white', line_dash=[10], line_width=3)

p.show(fig1)

Prepare result matrix for the data.

In [7]:

def create_markers_matrix(image_dataset):
    image_dataset_markers = []
    for img,markers in image_dataset:
        factor = 4.0
        target_shape = (int(round(img.shape[0]/factor)), int(round(img.shape[1]/factor)))
        markers_matrix = np.zeros(target_shape)
        for loc_x,loc_y,radius in markers:
            loc_x = loc_x / factor
            loc_y = loc_y / factor
            radius = radius / factor
            def value_at(x,y):
                value = 1.0 - math.sqrt((loc_x-x)**2 + (loc_y-y)**2)/radius
                return value if value > 0 else 0
            rr,cc = skimage.draw.circle(loc_y, loc_x, radius, shape = target_shape)
            for r,c in zip(rr, cc):
                markers_matrix[r,c] += value_at(c,r)
            markers_matrix /= np.max(markers_matrix)
        image_dataset_markers += [markers_matrix]
    return image_dataset_markers

image_dataset_markers = create_markers_matrix(image_dataset)
dataset_output_shape = image_dataset_markers[0].shape

In [ ]:
fig2_idx = 1

fig2 = p.figure(x_range=[0,1], y_range=[0,1])
fig2.image([image_dataset_markers[fig2_idx]], 0, 0, 1, 1, palette='Viridis256')
p.show(fig2)

Split dataset into train and test.

In [8]:
random.seed(1234)
np.random.seed(1234)

full_dataset = [(img[0].flatten(), matrix.flatten()) for img, matrix in zip(image_dataset, image_dataset_markers)]
full_dataset_train, full_dataset_test = \
    sklearn.model_selection.train_test_split(full_dataset, test_size = 0.3, random_state = 42)
print(len(full_dataset_train), len(full_dataset_test))

full_dataset_train = zip(*full_dataset_train)
full_dataset_test = zip(*full_dataset_test)

full_dataset_train = [np.array(x) for x in full_dataset_train]
full_dataset_test = [np.array(x) for x in full_dataset_test]

350 150


## 2. Try using MLP in TensorFlow

In [9]:

def nn_new_layer(input_tensor, layer_size, input_size, name = "", act = tf.sigmoid):
    with tf.name_scope("layer_" + name):
        with tf.name_scope("weights"):
            shape = (input_size, layer_size)
            weights = tf.Variable(tf.truncated_normal(shape, stddev=0.001))
#             weights = tf.Variable(tf.zeros(shape))
        with tf.name_scope("biases"):
            biases = tf.Variable(tf.constant(0.0, shape=[layer_size]))

        preact = tf.matmul(input_tensor, weights) + biases
        outputs = act(preact)
    return (outputs, preact)

def make_mlp_graph(input_size = (32,32), factor = 2.0, output_size = None, depth = 10, f_error = None,
                   default_act = tf.sigmoid, final_act = tf.identity):
    spaced_factors = np.linspace(1, factor**2, num=depth, dtype = int)
    print("Layer factors: ", spaced_factors)
    layer_sizes = ([np.prod(input_size)]*depth) // spaced_factors
    if output_size != None:
        layer_sizes[-1] = output_size
        for i in range(len(layer_sizes)):
            sz = layer_sizes[i]
            if sz < output_size:
                layer_sizes[i] = output_size
    print("Final layer sizes:", layer_sizes)
    
    with tf.name_scope("input_layer"):
        input_layer = tf.placeholder(tf.float32, shape=(None, layer_sizes[0]))
    
    with tf.name_scope("train_data"):
        train_data = tf.placeholder(tf.float32, shape=(None, layer_sizes[-1]))
        
    layers = [input_layer]
    for i in range(1,depth-1):
        layers += [nn_new_layer(layers[i-1], layer_sizes[i], layer_sizes[i-1], name = str(i), act = default_act)[0]]
    
    output_layer, logits = nn_new_layer(layers[-1], layer_sizes[-1], layer_sizes[-2], name = str("output"), act = final_act)
    layers += [output_layer]
    
    cross_entropy = f_error(train_data, logits)
    
    minimizer = tf.train.GradientDescentOptimizer(0.5).minimize(cross_entropy)
    
    return (input_layer, train_data, minimizer, output_layer)

# make_mlp_graph(input_size = dataset_image_shape, factor = 4.0)


First, try experimenting with MNIST data set, to verify that MLP is correct (basically).

In [ ]:
# Reset TF graph environment
tf.reset_default_graph()
random.seed(1234)
np.random.seed(1234)
tf.set_random_seed(1234)

session = tf.InteractiveSession()

In [ ]:
from tensorflow.examples.tutorials.mnist import input_data
mnist = input_data.read_data_sets('MNIST_data', one_hot=True)

In [ ]:
def f_error_softmax(train, result):
    return tf.nn.softmax_cross_entropy_with_logits(labels = train, logits = result)
input_layer, train_data, minimizer, output_layer = \
    make_mlp_graph(input_size = (28,28), factor=1.0, output_size = 10, depth = 2, f_error = f_error_softmax)

correct_prediction = tf.equal(tf.argmax(output_layer,1), tf.argmax(train_data,1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))

In [ ]:
tf.global_variables_initializer().run()

In [ ]:
for _ in range(200):
    batch = mnist.train.next_batch(100)
    minimizer.run(feed_dict={input_layer: batch[0], train_data: batch[1]})

In [ ]:
res = accuracy.eval(feed_dict={input_layer: mnist.test.images, train_data: mnist.test.labels})
res

Now try on our dataset.

Restart TF.

In [ ]:
tf.reset_default_graph()
random.seed(1234)
np.random.seed(1234)
tf.set_random_seed(1234)

session = tf.InteractiveSession()

In [ ]:
def f_error_l2(train, result):
#     return tf.nn.sigmoid_cross_entropy_with_logits(labels = train, logits = result)
    return tensorflow.losses.mean_squared_error(train, result)
input_layer, train_data, minimizer, output_layer = \
    make_mlp_graph(input_size = dataset_image_shape, factor=4.0, depth = 2, output_size=16*16,
                   f_error = f_error_l2, default_act = tf.nn.sigmoid, final_act = tf.nn.sigmoid)

accuracy = tf.sqrt(tf.reduce_mean(tf.squared_difference(train_data, output_layer)))

In [ ]:
tf.global_variables_initializer().run()

In [ ]:
for _ in range(500):
    minimizer.run(feed_dict={input_layer: full_dataset_train[0], train_data: full_dataset_train[1]})

In [ ]:
res = accuracy.eval(feed_dict={input_layer: full_dataset_test[0], train_data: full_dataset_test[1]})
res_train = accuracy.eval(feed_dict={input_layer: full_dataset_train[0], train_data: full_dataset_train[1]})
output_res = output_layer.eval(feed_dict={input_layer: full_dataset_test[0], train_data: full_dataset_test[1]})
output_res_train = output_layer.eval(feed_dict={input_layer: full_dataset_train[0], train_data: full_dataset_train[1]})
print(res, res_train)

In [ ]:
fig3_SHOW_SET = 4
fig3_USED_SET = (output_res, full_dataset_test)
# fig3_USED_SET = (output_res_train, full_dataset_train)

fig3_1 = p.figure(x_range=[0,1], y_range=[0,1])
fig3_2 = p.figure(x_range=[0,1], y_range=[0,1])
fig3_3 = p.figure(x_range=[0,1], y_range=[0,1])

fig3_1.image([fig3_USED_SET[1][0][fig3_SHOW_SET].reshape(64,64)], 0, 0, 1, 1, palette='Magma256')
fig3_2.image([fig3_USED_SET[1][1][fig3_SHOW_SET].reshape(16,16)], 0, 0, 1, 1, palette='Viridis256')
fig3_3.image([fig3_USED_SET[0][fig3_SHOW_SET].reshape(16,16)], 0, 0, 1, 1, palette='Viridis256')

p.show(bl.column(fig3_1, bl.row(fig3_2, fig3_3)))

In [ ]:
print(max(output_res[0]), min(output_res[0]))


## 3. Build Class 1 Neural Network and experiment

### Test creating index mapping

We need to build an index suitable for `tf.SparseTensor` function that will have random non-repeating values.

In [ ]:

random.seed(10)

selection_idx = random.sample(range(4096*4096), k=5)

selection = np.unravel_index(selection_idx, (4096,4096))

np.transpose(selection)

### Index mapping function

And also package this into a function.

In [9]:
%%cython  --compile-args=-O2 --compile-args=-fopenmp --link-args=-fopenmp

cimport cython
import numpy as np
cimport numpy as np
import math
import random

DTYPE = np.uint64
ctypedef np.uint64_t DTYPE_t
ctypedef unsigned long long uint64_t


@cython.boundscheck(False)
@cython.wraparound(False)
def fast_range_sample(uint64_t size, uint64_t k):
    """Reservoir sampling (approximated)"""
    
    cdef int BLOCK_SIZE = 2**int(math.log10(k) + 10)
    
    cdef uint64_t bl_start
    cdef uint64_t bl_end
    
    cdef np.ndarray[DTYPE_t, ndim=1] r = np.arange(k, dtype=DTYPE)
    cdef np.ndarray[DTYPE_t, ndim=1] rands
    
    for bl_start in range(k, size - BLOCK_SIZE, BLOCK_SIZE):
        bl_end = min(size, bl_start + BLOCK_SIZE)
        
        rands = np.random.randint(0, bl_end, size = bl_end - bl_start, dtype=DTYPE)
        idxs = np.where(rands < k)
        r[rands[idxs]] = np.array(idxs) + bl_start
    return r


@cython.boundscheck(False)
@cython.wraparound(False)
def fast_range_sample_faster(uint64_t size, long long k):
    """Reservoir sampling (approximated)"""
    
    cdef int BLOCK_SIZE = 2**int(math.log10(k) + 10)
    
    cdef long long bl_start
    cdef long long bl_end
    cdef long long bl_sz
    cdef long long i
    
    cdef np.ndarray[DTYPE_t, ndim=1] gs
    
    cdef double p
    cdef double u
    cdef uint64_t g
    
    cdef long long t = min(size, 4 * k)
    
    cdef np.ndarray[DTYPE_t, ndim=1] r = np.arange(k, dtype=DTYPE)
    cdef np.ndarray[DTYPE_t, ndim=1] rands
    cdef np.ndarray[DTYPE_t, ndim=1] idxsx
    
    for bl_start in range(k, max(t - BLOCK_SIZE, k + BLOCK_SIZE), BLOCK_SIZE):
        bl_end = min(size, bl_start + BLOCK_SIZE)
        rands = np.random.randint(0, bl_end, size = bl_end - bl_start, dtype=DTYPE)
        idxsx = np.where(rands < k)[0].astype(DTYPE)
        r[rands[idxsx]] = np.array((idxsx)) + bl_start

    bl_start = bl_end
    
    while bl_start < size:
        
        bl_end = min(size, bl_start + BLOCK_SIZE)

        bl_sz = bl_end - bl_start
        gs = np.zeros(bl_sz, dtype = DTYPE)
        i = 0
        
        while bl_start < size and i < bl_sz:
            p = k/bl_start
            u = 1-random.random()
            g = math.floor(math.log(u)/math.log(1-p))
            bl_start += g
            
            if bl_start < size:
                gs[i] = bl_start
                i += 1
        
        if i == 0:
            break
            
        if i < bl_sz:
            gs = gs[:i]
        
        r[np.random.randint(0,k, size = i, dtype=DTYPE)] = gs
        
        bl_start = max(bl_start, bl_end)
            
    return r





In [ ]:
%%timeit
fast_range_sample_faster(10**8, 5000)

In [10]:
def make_random_sparse_reservoir(input_size, shape):
    """
        Creates a mapping from vector of shape (input_size) to a sparse matrix of shape shape.
        Returns indices of a sparse matrix built from a vector of size input_size
    """
    selection_idx = np.sort(fast_range_sample_faster(np.prod(shape), k=input_size))

    selection = np.transpose(np.unravel_index(selection_idx, shape))
    
    return selection

def make_random_sparse_select(input_size, shape):
    """
        Creates a mapping from vector of shape (input_size) to a sparse matrix of shape shape.
        Returns indices of a sparse matrix built from a vector of size input_size
    """
    selection_idx = np.sort(random.sample(range(np.prod(shape)), k=input_size))

    selection = np.transpose(np.unravel_index(selection_idx, shape))
    
    return selection


In [ ]:
%timeit make_random_sparse_select(1000000, (10000, 10000))

In [ ]:
%timeit make_random_sparse_reservoir(10000000, (10000, 10000))

In [ ]:
d = make_random_sparse_reservoir(100000, (10000, 10000))

np.mean(d)

When input_size reaches 10 000 000, `random.sample` can't fit in memory anymore…

In [11]:
def make_random_sparse(input_size, shape):
    if input_size < 5000000:
        return make_random_sparse_select(input_size, shape)
    else:
        return make_random_sparse_reservoir(input_size, shape)



### Test statistics of index mapping function

And then test statistical properties. It needs to be same as for a uniform distribution for each axis independently.

We test 1000 samples of shape $(1001,1001)$. That means, that each axis should have a uniform distribution in $[0;1000]$. That gives it expectation of $M = \frac{1}{2} (1000 + 0) = 500$ and standard deviation
$ \sigma = \sqrt{ \frac{1}{12} (1000 - 0)^{2} } \approx 288.68 $.



In [ ]:
x = np.array([])
y = np.array([])
print("|--------|")
for i in range(1000):
    if i % 100 == 0:
        print('*', end = '')
    x1, y1 = np.transpose(make_random_sparse_select(1000, (1001, 1001)))
    x = np.concatenate((x, x1))
    y = np.concatenate((y, y1))
Math(f"\\begin{{align}} \
M(x) & = {np.mean(x)} \\\\ \
\\sigma(x) & = {np.std(x)} \\\\ \
M(y) & = {np.mean(y)} \\\\ \
\\sigma(y) & = {np.std(y)} \\\\ \
\\end{{align}}")

In [ ]:
x = np.array([])
y = np.array([])
print("|--------|")
for i in range(1000):
    if i % 100 == 0:
        print('*', end = '')
    x1, y1 = np.transpose(make_random_sparse_reservoir(1000, (1001, 1001)))
    x = np.concatenate((x, x1))
    y = np.concatenate((y, y1))
Math(f"\\begin{{align}} \
M(x) & = {np.mean(x)} \\\\ \
\\sigma(x) & = {np.std(x)} \\\\ \
M(y) & = {np.mean(y)} \\\\ \
\\sigma(y) & = {np.std(y)} \\\\ \
\\end{{align}}")

Good stats!

Well, if you are asking why there is Cython, progress meters, etc, just try this for a bigger neural net ;) It was designed and built for bigger tasks, and this one is pretty small.

So if we will be going to build Class 2 or higher neural nets, we would probably prefer to round that last number. We can drop some indices, right?

### Utility functions for neural network

In [7]:
def nn_layer_sizes(factor, input_size, output_size, depth):
    """
        Creates sizes for neural network with reducing sizes specified by factor. Input
    """
    try:
        len(factor)
        spaced_factors = np.array(factor)
    except:
        spaced_factors = np.linspace(1, factor, num=depth, dtype = np.float64)
    layer_sizes = np.asarray(([input_size]*depth) / spaced_factors, dtype=np.int)
    if output_size != None:
        layer_sizes[-1] = output_size
    return layer_sizes

def weight_matrices_shapes_for_layers(layer_sizes):
    shapes = []
    for i in range(1, len(layer_sizes)):
        shape = (layer_sizes[i-1], layer_sizes[i])
        shapes += [shape]
        
    return shapes

def weights_for_shapes(shapes):
    return [np.prod(s) for s in shapes]
    

def sparse_from_dense_factored(dense_shape, fraction):
    """
        Creates indices for sparse matrix from the dense_shape with randomized
        elements. Count of elements present is fraction * prod(dense_shape)
    """
    out_count = math.floor(np.prod(dense_shape) * fraction)
    res_indices = make_random_sparse(out_count, dense_shape)
        
    return res_indices

def weights_sparse_indices(weights_shapes, fractions):
    return [sparse_from_dense_factored(shape, fraction) if fraction != None else None for shape,fraction in zip(weights_shapes,fractions)]

def weights_size_shapes_indices(shapes, indices):
    return [len(idx) if None != idx else np.prod(shape) for shape,idx in zip(shapes,indices)]


Now let's create a special class to hold configuration that will be easy to use and see.

In [87]:

class StructMeta(type):
    
    __RECURSION = []
    
    def __new__(cls, name, bases, attrs):
        return super(StructMeta, cls).__new__(cls, name, bases, attrs)
    
    def __init__(self, name, bases, attrs):
        super(StructMeta, self).__init__(name, bases, attrs)
        self.__sm_parents = []
        for k,v in attrs.items():
            if type(v) == StructMeta:
                v.__sm_parents += [self]
        
    def _rawlist(self):
        if self in StructMeta.__RECURSION:
            return None
        StructMeta.__RECURSION += [self] + self.__sm_parents
        attrs = self._allattrs()
        names = [k for k,_ in attrs.items()]
        result = []
        try:
            for attrname, attrvalue in attrs.items():
                if type(attrvalue) != StructMeta:
                    result += [f"{attrname}: {attrvalue}"]
                else:
                    r = attrvalue._rawlist()
                    if r == None:
                        result += [f"{attrname}: {object.__repr__(attrvalue)}"]
                    else:
                        result += [(attrname, r)]
        except RecursionError as e:
            print(f"{self.__name__} has recursive definition. Attributes of it: {names}")
            raise e
        StructMeta.__RECURSION = StructMeta.__RECURSION[:-len(self.__sm_parents)-1]
        return result
    
    def __setattr__(self, attr, value):
        if type(value) == StructMeta:
            value.__sm_parents += self
        return type.__setattr__(self, attr, value)
        
    def __str__(self):
        ls = self._rawlist()
        if ls == None:
            return type.__str__(self)
        else:
            return self._linetab_str(ls)
    
    def __repr__(self):
        ls = self._rawlist()
        if ls == None:
            return type.__repr__(self)
        else:
            return self._linetab_repr(ls) + "\n}"
    
    def _allattrs(self):
        builtin = ['__module__', '__qualname__', '__doc__', '_StructMeta__sm_parents']
        return dict([(n,a) for n,a in self.__dict__.items() if n not in builtin])
    
    @staticmethod
    def _linetab_repr(lines, tab = '   ', true_tab = None):
        if true_tab == None: true_tab = tab
        s = "{\n" + true_tab
        s += (', \n' + true_tab).join([
            l if type(l) == str
            else f"{l[0]}: " + StructMeta._linetab_repr(l[1], tab=tab, true_tab=tab+true_tab) + "\n" + true_tab + "}"
            for l in lines
        ])
        return s
    
    @staticmethod
    def _linetab_str(lines, tab = ''):
        return "\n".join([
            tab + l if type(l) == str
            else StructMeta._linetab_str(l[1], tab=f"{tab}{l[0]}.",)
            for l in lines
        ])

class ReprStruct(object, metaclass = StructMeta): pass
    

### Class 1A Neural Network implementation

Variant A tries to use static randomly selected weights to reduce complexity.

In [14]:
class ClassOneNN(object):
    
    DTYPE_INT = tf.int32
    DTYPE_FLOAT = tf.float32
    
    def __init__(self, config):
        super(ClassOneNN, self).__init__()
        
        self.config = config
    
    def setup_nn(self):
        config = self.config
        with tf.name_scope("layer-1"):
            input_tensor = tf.placeholder(self.DTYPE_FLOAT, shape=(None, config.L1.LAYER_SZ[0]))
            
            l1_layers = [input_tensor]
            
            for i in range(config.L1.DEPTH-1):
                weights = self.nn_weights_for_layer(config.L1.WEIGHTS_SHAPES[i])
                biases = self.nn_biases_for_layer(config.L1.LAYER_SZ[i+1])
                layer_out, layer_pre = self.nn_layer(l1_layers[-1], weights, biases, act = config.L1.ACTS[i])
                l1_layers += [layer_out]
            
            l1_out = l1_layers[-1]
            l1_preout = layer_pre
        
        with tf.name_scope("layer-0"):
            l0_layers = [input_tensor]
            
            t = 0
            for i in range(config.L0.DEPTH-1):
                if config.L0.SPARSITY[i] != None:
                    sample_size = tf.gather(tf.shape(l1_out, out_type=self.DTYPE_INT), 0)
                    indices_0 = tf.constant(config.L0.WEIGHTS_INDICES[i], dtype=self.DTYPE_INT)
                    indices_1 = tf.tile(indices_0, tf.stack([sample_size, 1]))
                    indices_2 = tf.reshape(tf.tile(tf.expand_dims(tf.range(sample_size, dtype=self.DTYPE_INT),1),
                                                   tf.constant([1, config.L0.WEIGHTS_SZ[i]], dtype=self.DTYPE_INT)),
                                           [-1,1])
                    indices = tf.concat([indices_2, indices_1], 1)
                    weights_shape = tf.concat([tf.expand_dims(sample_size,0),
                                               tf.constant(config.L0.WEIGHTS_SHAPES[i], dtype=self.DTYPE_INT)],
                                              0)
                    values = tf.reshape(tf.slice(l1_out, (0,t), (-1,config.L0.WEIGHTS_SZ[i])),
                                        tf.expand_dims(sample_size * config.L0.WEIGHTS_SZ[i], 0))
                    weights = tf.sparse_to_dense(indices, weights_shape, values)
                else:
                    sample_size = tf.gather(tf.shape(l1_out, out_type=self.DTYPE_INT), 0)
                    weights_shape = tf.concat([tf.expand_dims(sample_size,0),
                                               tf.constant(config.L0.WEIGHTS_SHAPES[i], dtype=self.DTYPE_INT)],
                                              0)
                    weights = tf.reshape(tf.slice(l1_out, (0,t), (-1,config.L0.WEIGHTS_SZ[i])),
                                       weights_shape)
                biases = self.nn_biases_for_layer(config.L0.LAYER_SZ[i+1])
                layer_out, layer_pre = self.nn_layer(tf.expand_dims(l0_layers[-1],1), weights, biases,
                                                act = config.L0.ACTS[i], mul = tf.matmul)
                layer_out = tf.squeeze(layer_out)
                layer_pre = tf.squeeze(layer_pre)
                l0_layers += [layer_out]
                
                t += config.L0.WEIGHTS_SZ[i]
            
            l0_out = l0_layers[-1]
            l0_preout = layer_pre
            
            self.input_tensor = input_tensor
            self.l1_out = l1_out
            self.l1_preout = l1_preout
            self.l1_layers = l1_layers
            self.l0_out = l0_out
            self.l0_preout = l0_preout
            self.l0_layers = l0_layers
            
    def setup_error(self, f_error, optimizer, optimizer_args):
        with tf.name_scope("train"):
            train_tensor = tf.placeholder(self.DTYPE_FLOAT, shape=(None, self.config.OUTPUT_SIZE))
            error_tensor = f_error(train_tensor, self.l0_preout)
            minimizer = optimizer(*optimizer_args).minimize(error_tensor)
            
        self.train_tensor = train_tensor
        self.minimizer_tensor = minimizer
        self.error_tensor = error_tensor

    @staticmethod
    def nn_weights_for_layer(shape):
        with tf.name_scope("weights"):
            return tf.Variable(tf.truncated_normal(shape, stddev=0.001, dtype=ClassOneNN.DTYPE_FLOAT))

    @staticmethod
    def nn_biases_for_layer(layer_size):
        with tf.name_scope("biases"):
            return tf.Variable(tf.constant(0.0, shape=[layer_size], dtype=ClassOneNN.DTYPE_FLOAT))

    @staticmethod
    def nn_layer(input_tensor, weights_tensor, biases_tensor, act = tf.sigmoid, mul = tf.matmul):
        preact = mul(input_tensor, weights_tensor) + biases_tensor
        outputs = act(preact)
        return (outputs, preact)


### Trying out on MNIST

In [15]:
random.seed(1234)
np.random.seed(1234)

class NNClassOne_Cfg_0(ReprStruct):
    
    INPUT_SIZE = 28*28
    OUTPUT_SIZE = 10
    
    class L0(ReprStruct): pass
    class L1(ReprStruct): pass
    
        
    L0.INPUT_SIZE = INPUT_SIZE
    L0.OUTPUT_SIZE = OUTPUT_SIZE
    L0.DEPTH = 2
#     L0.DEPTH = 3
    L0.FACTOR = 1
#     L0.FACTOR = [1, 4, 1]
    L0.LAYER_SZ = nn_layer_sizes(L0.FACTOR, L0.INPUT_SIZE, L0.OUTPUT_SIZE, L0.DEPTH)
    L0.WEIGHTS_SHAPES = weight_matrices_shapes_for_layers(L0.LAYER_SZ)
    L0.ACTS = [tf.identity]
#     L0.ACTS = [tf.nn.relu, tf.identity]
    
    L0.SPARSITY = [None]
#     L0.SPARSITY = [None, None]
    L0.WEIGHTS_INDICES = weights_sparse_indices(L0.WEIGHTS_SHAPES, L0.SPARSITY)
    L0.WEIGHTS_SZ = weights_size_shapes_indices(L0.WEIGHTS_SHAPES, L0.WEIGHTS_INDICES)
    
    L1.INPUT_SIZE = INPUT_SIZE
    L1.OUTPUT_SIZE = sum(L0.WEIGHTS_SZ)
    L1.DEPTH = 2
#     L1.DEPTH = 3
#     L1.DEPTH = 4
    L1.FACTOR = [1, 1]
#     L1.FACTOR = [1, 1./4, 1]
#     L1.FACTOR = [1, 1./4, 1./4, 1]
    L1.LAYER_SZ = nn_layer_sizes(L1.FACTOR, L1.INPUT_SIZE, L1.OUTPUT_SIZE, L1.DEPTH)
    L1.WEIGHTS_SHAPES = weight_matrices_shapes_for_layers(L1.LAYER_SZ)
    L1.ACTS = [tf.identity]
#     L1.ACTS = [tf.nn.sigmoid, tf.identity]
#     L1.ACTS = [tf.nn.sigmoid, tf.nn.sigmoid, tf.nn.tanh]



In [ ]:
NNClassOne_Cfg_0

In [ ]:
# Reset TF graph environment
try:
    del nn0
    del accuracy
    session.close()
    del session
except:
    pass

tf.reset_default_graph()
random.seed(1234)
np.random.seed(1234)
tf.set_random_seed(1234)

session = tf.InteractiveSession()

In [16]:
from tensorflow.examples.tutorials.mnist import input_data
mnist = input_data.read_data_sets('MNIST_data', one_hot=True)

Extracting MNIST_data/train-images-idx3-ubyte.gz
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz


In [ ]:
def f_error_softmax(train, result):
    return tf.nn.softmax_cross_entropy_with_logits(labels = train, logits = result)

nn0 = ClassOneNN(NNClassOne_Cfg_0)
nn0.setup_nn()
nn0.setup_error(f_error_softmax, tf.train.GradientDescentOptimizer, [0.1])

correct_prediction = tf.equal(tf.argmax(nn0.l0_out,1), tf.argmax(nn0.train_tensor,1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))


In [ ]:
tf.global_variables_initializer().run()

In [ ]:
acc_vec = []

for i in range(200):
    if i % 2 == 0:
        print(f"{i//2}%", end=' ')
    if i % 20 == 0:
        acc_vec += [(
            accuracy.eval(feed_dict={nn0.input_tensor: mnist.train.images[:100], nn0.train_tensor: mnist.train.labels[:100]}),
            accuracy.eval(feed_dict={nn0.input_tensor: mnist.test.images[:100], nn0.train_tensor: mnist.test.labels[:100]})
        )]
        print('.', end=' ')
    batch = mnist.train.next_batch(100)
    nn0.minimizer_tensor.run(feed_dict={nn0.input_tensor: batch[0], nn0.train_tensor: batch[1]})

acc_vec += [(
    accuracy.eval(feed_dict={nn0.input_tensor: mnist.train.images[:100], nn0.train_tensor: mnist.train.labels[:100]}),
    accuracy.eval(feed_dict={nn0.input_tensor: mnist.test.images[:100], nn0.train_tensor: mnist.test.labels[:100]})
)]
print('. 100%')

In [ ]:
res = accuracy.eval(feed_dict={nn0.input_tensor: mnist.test.images[:100], nn0.train_tensor: mnist.test.labels[:100]})
res

In [ ]:
# NOTE: this may crash due to memory limits
res = accuracy.eval(feed_dict={nn0.input_tensor: mnist.test.images, nn0.train_tensor: mnist.test.labels})
res

In [ ]:
m = tf.reduce_mean(nn0.l1_out, axis=0)
v = tf.reduce_max(tf.square(nn0.l1_out - m), axis=0)
mean, variance, weights_out = session.run((m, v, nn0.l1_out), feed_dict={nn0.input_tensor: mnist.test.images, nn0.train_tensor: mnist.test.labels})

In [ ]:
fig4_1 = p.figure(x_axis_label='Iterations', y_axis_label='Accuracy')

fig4_1.line(range(0, len(acc_vec)*100, 100), [x[0] for x in acc_vec], line_color='blue', legend='Train')
fig4_1.square(range(0, len(acc_vec)*100, 100), [x[0] for x in acc_vec], color='blue')
fig4_1.line(range(0, len(acc_vec)*100, 100), [x[1] for x in acc_vec], line_color='red', legend='Test')
fig4_1.square(range(0, len(acc_vec)*100, 100), [x[1] for x in acc_vec], color='red')

fig4_1.legend.location = 'top_left'
p.show(fig4_1)

In [ ]:
fig4_2 = p.figure(x_range=[0,28*28], y_range=[0,10], x_axis_label='Input', y_axis_label='Output', title='Mean weights')
fig4_2.image([mean.reshape(28*28,10).T], 0, 0, 28*28, 10, palette='Magma256')

fig4_3 = p.figure(x_range=[0,28*28], y_range=[0,10], x_axis_label='Input', y_axis_label='Output', title='Weights variance')
fig4_3.image([variance.reshape(28*28,10).T], 0, 0, 28*28, 10, palette='Magma256')

p.show(bl.row(fig4_2, fig4_3))

In [ ]:
fig4_2s = []
fig4_3s = []

for i in range(10):
    fig4_2_i = p.figure(x_range=[0,28], y_range=[28,0], title=f"Mean weights {i}")
    fig4_2_i.image([mean.reshape(28*28,10).T[i,:].reshape(28,28)[::-1,:]], 0, 28, 28, 28, palette='Magma256')
    fig4_2s += [fig4_2_i]
    
    fig4_3_i = p.figure(x_range=[0,28], y_range=[28,0], title=f"Weights variance {i}")
    fig4_3_i.image([variance.reshape(28*28,10).T[i,:].reshape(28,28)[::-1,:]], 0, 28, 28, 28, palette='Magma256')
    fig4_3s += [fig4_3_i]

p.show(bl.gridplot(fig4_2s, fig4_3s, plot_width=200, plot_height=200))

In [ ]:
fig4_4s = []
fig4_idx = 0

for i in range(10):
    fig4_4_i = p.figure(x_range=[0,28], y_range=[28,0], title=f"Mean weights {i} at Test f{fig4_idx}")
    fig4_4_i.image([weights_out[fig4_idx].reshape(28*28,10).T[i,:].reshape(28,28)[::-1,:]], 0, 28, 28, 28, palette='Magma256')
    fig4_4s += [fig4_4_i]

p.show(bl.gridplot([fig4_4s], plot_width=200, plot_height=200))

In [ ]:
fig4_5 = p.figure(x_range=[0,28], y_range=[28,0], title="Test f{fig4_idx}", plot_width=200, plot_height=200)
fig4_5.image([np.array(mnist.test.images[fig4_idx]).reshape(28,28)[::-1,:]], 0, 28, 28, 28)

p.show(fig4_5)

Beyond that, I also tried dephth-2 and dephth-4 configurations. Dephth-2 performed quite bad, and dephth-4 went with even less variance.

So thinking on that, I find it good but… totally not enough. After some looong thinking I came to an optimization, that may just yield what I search for.

Behold, *Gaussian Selectrick* ;)

### Class 1A + Gaussian Selectrick Implementation

Ok, here we intend to add a special layer between layer-1 and layer-2 networoks: gaussian selectrick. We limit the size of the layer-1 network output to a certain number and map it on layer-1 weights using gaussian distribution. $\sigma$ and $\mu$ are declared as variables and will be updated during the training process, yielding a (hopefully) smart enough choice of what weights will need to be mapped.

In [94]:
class ClassOneSTNN(object):
    
    DTYPE_INT = tf.int32
    DTYPE_FLOAT = tf.float32
    
    def __init__(self, config):
        super(ClassOneSTNN, self).__init__()
        
        self.config = config
    
    def setup_nn(self):
        config = self.config
        
        input_tensor = tf.placeholder(self.DTYPE_FLOAT, shape=(None, config.L1.LAYER_SZ[0]))
        phase = tf.placeholder(tf.bool, name='phase')
        self.phase = phase
        
        sample_size = tf.gather(tf.shape(input_tensor, out_type=self.DTYPE_INT), 0)
        
        with tf.name_scope("layer-1"):
            
            l1_layers = [input_tensor]
            
            for i in range(config.L1.DEPTH-1):
                weights = self.nn_weights_for_layer(config.L1.WEIGHTS_SHAPES[i], stddev=config.L1.STDDEV[i])
                biases = self.nn_biases_for_layer(config.L1.LAYER_SZ[i+1], value=config.L1.BIAS[i])
                layer_out, layer_pre = self.nn_layer(l1_layers[-1], weights, biases, act = config.L1.ACTS[i])
                l1_layers += [layer_out]
            
            l1_out = l1_layers[-1]
            l1_preout = layer_pre
        
        with tf.name_scope("selectrick"):
            
            lst_outs = []
            layers_out = []
            weights_init = [[[random.gauss(0,config.ST.STDDEV) for i in range(config.ST.MEDIAL_SIZE)]]]*config.ST.INPUT_SIZE
            weights_pre = tf.Variable(tf.constant(weights_init, dtype=self.DTYPE_FLOAT))
            weights = config.ST.WEIGHTSACT(weights_pre)
            biases = tf.Variable(tf.constant([random.gauss(0,config.ST.BIAS) for _ in range(config.ST.OUTPUT_SIZE)], dtype=self.DTYPE_FLOAT))
            lst_preform = tf.transpose(tf.expand_dims(l1_out,2), [1,0,2]) @ weights
            lst_form = tf.reshape(tf.transpose(lst_preform, [1,0,2]), [-1, config.ST.OUTPUT_SIZE])
            lst_shuffle = config.ST.SHUFFLE(lst_form)
            lst_out = lst_shuffle + biases
        
        with tf.name_scope("layer-0"):
            l0_layers = [input_tensor]
            
            t = 0
            for i in range(config.L0.DEPTH-1):
                weights = tf.reshape(tf.slice(lst_out, (0,t), (-1,config.L0.WEIGHTS_SZ[i])),
                                   [-1] + list(config.L0.WEIGHTS_SHAPES[i]))
                biases = self.nn_biases_for_layer(config.L0.LAYER_SZ[i+1], value=config.L0.BIAS[i])
                layer_out, layer_pre = self.nn_layer(tf.expand_dims(l0_layers[-1],1), weights, biases,
                                                act = config.L0.ACTS[i], mul = tf.matmul, with_norm = config.L0.NORM[i])
                layer_out = tf.squeeze(layer_out)
                layer_pre = tf.squeeze(layer_pre)
                l0_layers += [layer_out]

                t += config.L0.WEIGHTS_SZ[i]
            
            l0_out = l0_layers[-1]
            l0_preout = layer_pre
            
            self.input_tensor = input_tensor
            self.l1_out = l1_out
            self.l1_preout = l1_preout
            self.l1_layers = l1_layers
            self.lst_out = lst_out
            self.l0_out = l0_out
            self.l0_preout = l0_preout
            self.l0_layers = l0_layers
            
    def setup_error(self, f_error, optimizer, optimizer_args):
        with tf.name_scope("train"):
            update_ops = tf.get_collection(tf.GraphKeys.UPDATE_OPS)
            with tf.control_dependencies(update_ops):
                train_tensor = tf.placeholder(self.DTYPE_FLOAT, shape=(None, self.config.OUTPUT_SIZE))
            error_tensor = f_error(train_tensor, self.l0_preout)
            minimizer = optimizer(*optimizer_args).minimize(error_tensor)
            
        self.train_tensor = train_tensor
        self.minimizer_tensor = minimizer
        self.error_tensor = error_tensor

    @staticmethod
    def nn_weights_for_layer(shape, stddev=0.001):
        with tf.name_scope("weights"):
            return tf.Variable(tf.truncated_normal(shape, stddev=stddev, dtype=ClassOneSTNN.DTYPE_FLOAT))

    @staticmethod
    def nn_biases_for_layer(layer_size, value = 0.0):
        with tf.name_scope("biases"):
            return tf.Variable(tf.constant(value, shape=[layer_size], dtype=ClassOneSTNN.DTYPE_FLOAT))

    def nn_layer(self, input_tensor, weights_tensor, biases_tensor, act = tf.sigmoid, mul = tf.matmul, with_norm = False):
        preact = mul(input_tensor, weights_tensor) + biases_tensor
        if with_norm:
            preact = tf.contrib.layers.batch_norm(preact, center=True, scale=True, is_training=self.phase)
        outputs = act(preact)
        return (outputs, preact)


In [237]:
w = tf.constant([[0.1,0.2],[0.2,0.3]])
x = tf.constant([[1.0,1.0],[2.0,2.0],[3.0,3.0],[4.0,4.0]])
b = tf.constant([100.0, 200.0])
print(w.eval())
print(x.eval())
print((x @ w + b).eval())

[[ 0.1         0.2       ]
 [ 0.2         0.30000001]]
[[ 1.  1.]
 [ 2.  2.]
 [ 3.  3.]
 [ 4.  4.]]
[[ 100.30000305  200.5       ]
 [ 100.59999847  201.        ]
 [ 100.90000153  201.5       ]
 [ 101.19999695  202.        ]]


In [238]:
w = tf.constant([[[0.1,0.2],[0.2,0.3]]]*4)
x = tf.constant([[1.0,1.0],[2.0,2.0],[3.0,3.0],[4.0,4.0]])
b = tf.constant([100.0, 200.0])
print(w.eval())
print(x.eval())
print(tf.squeeze(tf.expand_dims(x,1) @ w + b).eval())

[[[ 0.1         0.2       ]
  [ 0.2         0.30000001]]

 [[ 0.1         0.2       ]
  [ 0.2         0.30000001]]

 [[ 0.1         0.2       ]
  [ 0.2         0.30000001]]

 [[ 0.1         0.2       ]
  [ 0.2         0.30000001]]]
[[ 1.  1.]
 [ 2.  2.]
 [ 3.  3.]
 [ 4.  4.]]
[[ 100.30000305  200.5       ]
 [ 100.59999847  201.        ]
 [ 100.90000153  201.5       ]
 [ 101.19999695  202.        ]]


### Class 1A + Seltrick on MNIST dataset

#### Configurations

In [88]:
random.seed(1234)
np.random.seed(1234)

class NNClassOneST_Cfg_0(ReprStruct):
    
    INPUT_SIZE = 28*28
    OUTPUT_SIZE = 10
    
    class L0(ReprStruct): pass
    class ST(ReprStruct): pass
    class L1(ReprStruct): pass
    
        
    L0.INPUT_SIZE = INPUT_SIZE
    L0.OUTPUT_SIZE = OUTPUT_SIZE
    L0.DEPTH = 2
    L0.FACTOR = 1
    L0.LAYER_SZ = nn_layer_sizes(L0.FACTOR, L0.INPUT_SIZE, L0.OUTPUT_SIZE, L0.DEPTH)
    L0.WEIGHTS_SHAPES = weight_matrices_shapes_for_layers(L0.LAYER_SZ)
    L0.ACTS = [tf.identity]
    L0.BIAS = [0.1, 0.0]
    
    L0.WEIGHTS_SZ = weights_for_shapes(L0.WEIGHTS_SHAPES)
    
    ST.MEDIAL_SIZE = 20
    
    L1.INPUT_SIZE = INPUT_SIZE
    L1.OUTPUT_SIZE = int(sum(L0.WEIGHTS_SZ) // ST.MEDIAL_SIZE)
    L1.DEPTH = 2
    L1.FACTOR = [1, 1]
    L1.LAYER_SZ = nn_layer_sizes(L1.FACTOR, L1.INPUT_SIZE, L1.OUTPUT_SIZE, L1.DEPTH)
    L1.WEIGHTS_SHAPES = weight_matrices_shapes_for_layers(L1.LAYER_SZ)
    L1.ACTS = [tf.identity]
    L1.BIAS = [0.0]
    L1.STDDEV = [0.001]

    ST.INPUT_SIZE = L1.OUTPUT_SIZE
    ST.OUTPUT_SIZE = sum(L0.WEIGHTS_SZ)
    ST.STDDEV = 0.001
    ST.BIAS = 0.01
    ST.WEIGHTSACT = tf.nn.softmax
    
    @classmethod
    def st_shuffle(self, x):
        return tf.transpose(tf.gather(tf.transpose(x), self.ST.MAP))
    
    ST.SHUFFLE = st_shuffle
    
    @classmethod
    def _stmapgen(self):
        t = list(range(self.ST.OUTPUT_SIZE))
        random.shuffle(t)
        return t
    
    ST.MAP = []
    
    
    assert ST.OUTPUT_SIZE == ST.INPUT_SIZE * ST.MEDIAL_SIZE, "ST.MEDIAL_SIZE and ST.OUTPUT_SIZE don't match (probably division error)"

NNClassOneST_Cfg_0.ST.MAP = NNClassOneST_Cfg_0._stmapgen()

random.seed(1234)
np.random.seed(1234)

class NNClassOneST_Cfg_1(ReprStruct):
    
    INPUT_SIZE = 28*28
    OUTPUT_SIZE = 10
    
    class L0(ReprStruct): pass
    class ST(ReprStruct): pass
    class L1(ReprStruct): pass
    
        
    L0.INPUT_SIZE = INPUT_SIZE
    L0.OUTPUT_SIZE = OUTPUT_SIZE
    L0.DEPTH = 3
    L0.FACTOR = [1, 4, 1]
    L0.LAYER_SZ = nn_layer_sizes(L0.FACTOR, L0.INPUT_SIZE, L0.OUTPUT_SIZE, L0.DEPTH)
    L0.WEIGHTS_SHAPES = weight_matrices_shapes_for_layers(L0.LAYER_SZ)
    L0.ACTS = [tf.nn.elu, tf.identity]
    L0.NORM = [True, False]
    L0.BIAS = [0.1, 0.0]
    
    L0.WEIGHTS_SZ = weights_for_shapes(L0.WEIGHTS_SHAPES)
    
    ST.MEDIAL_SIZE = 28
    
    L1.INPUT_SIZE = INPUT_SIZE
    L1.OUTPUT_SIZE = int(sum(L0.WEIGHTS_SZ) // ST.MEDIAL_SIZE)
    L1.DEPTH = 2
    L1.FACTOR = [1, 1]
    L1.LAYER_SZ = nn_layer_sizes(L1.FACTOR, L1.INPUT_SIZE, L1.OUTPUT_SIZE, L1.DEPTH)
    L1.WEIGHTS_SHAPES = weight_matrices_shapes_for_layers(L1.LAYER_SZ)
    L1.ACTS = [tf.identity]
    L1.BIAS = [0.0]
    L1.STDDEV = [0.001]

    ST.INPUT_SIZE = L1.OUTPUT_SIZE
    ST.OUTPUT_SIZE = sum(L0.WEIGHTS_SZ)
    ST.STDDEV = 0.1
    ST.BIAS = 0.1
    ST.WEIGHTSACT = tf.nn.softmax
    
    @classmethod
    def st_shuffle(self, x):
        return tf.transpose(tf.gather(tf.transpose(x), self.ST.MAP))
#         return tf.zeros_like(x)

    ST.SHUFFLE = tf.identity
    
    @classmethod
    def _stmapgen(self):
        m = np.reshape(np.indices((4,7)), [2,-1])
        mg = np.ravel([np.ravel([np.ravel_multi_index(m + np.array([[i*4,j*7]]*28).T, (28,28)) for i in range(7)]) for j in range(4)])
        t = set(range(self.ST.OUTPUT_SIZE))
        r = list(t - set(mg))
        random.shuffle(r)
        return list(mg) + r
    
    ST.MAP = []
    
    assert ST.OUTPUT_SIZE == ST.INPUT_SIZE * ST.MEDIAL_SIZE, \
        f"ST.MEDIAL_SIZE and ST.OUTPUT_SIZE don't match (probably division error). {ST.OUTPUT_SIZE}//{ST.MEDIAL_SIZE} != {ST.INPUT_SIZE}"

NNClassOneST_Cfg_1.ST.MAP = NNClassOneST_Cfg_1._stmapgen()
NNClassOneST_Cfg_1.ST.SHUFFLE = NNClassOneST_Cfg_1.st_shuffle


#### Configuration 0

In [23]:
NNClassOneST_Cfg_0

{
   INPUT_SIZE: 784, 
   OUTPUT_SIZE: 10, 
   L0: {
      INPUT_SIZE: 784, 
      OUTPUT_SIZE: 10, 
      DEPTH: 2, 
      FACTOR: 1, 
      LAYER_SZ: [784  10], 
      WEIGHTS_SHAPES: [(784, 10)], 
      ACTS: [<function identity at 0x7f3b136ff268>], 
      WEIGHTS_SZ: [7840]
   }, 
   ST: {
      INPUT_SIZE: 392, 
      OUTPUT_SIZE: 7840, 
      MEDIAL_SIZE: 20, 
      MAP: [161, 2213, 1412, 5118, 3836, 293, 265, 3242, 5557, 436, 5055, 670, 3198, 3032, 5786, 7774, 6324, 4133, 2151, 383, 2217, 5960, 6897, 4632, 4728, 4209, 6671, 1151, 2538, 7683, 27, 3172, 7376, 5935, 7622, 6286, 348, 7837, 2768, 7232, 5994, 5964, 3856, 6087, 4871, 6802, 752, 959, 5836, 1443, 5506, 3912, 5503, 2614, 5205, 2148, 2556, 1681, 3975, 1235, 2505, 4781, 510, 7820, 3809, 1475, 2317, 6845, 6012, 4686, 7781, 7045, 4526, 362, 1911, 337, 7300, 5512, 7588, 3555, 3531, 1419, 2111, 6501, 5060, 3888, 2621, 7348, 6189, 5857, 1462, 6105, 2825, 2050, 5792, 7305, 7142, 5539, 5513, 3150, 6407, 1817, 3382, 5135, 4182, 714

In [62]:
# Reset TF graph environment
try:
    del nn0
    del accuracy
    session.close()
    del session
except:
    pass

tf.reset_default_graph()
random.seed(1234)
np.random.seed(1234)
tf.set_random_seed(1234)

session = tf.InteractiveSession()

In [63]:
from tensorflow.examples.tutorials.mnist import input_data
mnist = input_data.read_data_sets('MNIST_data', one_hot=True)

Extracting MNIST_data/train-images-idx3-ubyte.gz
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz


In [64]:
def f_error_softmax(train, result):
    return tf.nn.softmax_cross_entropy_with_logits(labels = train, logits = result)

nn1 = ClassOneSTNN(NNClassOneST_Cfg_0)
nn1.setup_nn()
nn1.setup_error(f_error_softmax, tf.train.GradientDescentOptimizer, [0.1])

correct_prediction = tf.equal(tf.argmax(nn1.l0_out,1), tf.argmax(nn1.train_tensor,1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))


/usr/local/lib/python3.6/dist-packages/tensorflow/python/ops/gradients_impl.py:93: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


In [65]:
tf.global_variables_initializer().run()

In [66]:
acc_vec = []

train_iters = 2000

for i in range(train_iters):
    if i % (train_iters//100) == 0:
        print(f"{i//(train_iters//100)}%", end=' ')
    if i % (train_iters//20) == 0:
        acc_vec += [(
            accuracy.eval(feed_dict={nn1.input_tensor: mnist.train.images[:100], nn1.train_tensor: mnist.train.labels[:100]}),
            accuracy.eval(feed_dict={nn1.input_tensor: mnist.test.images[:100], nn1.train_tensor: mnist.test.labels[:100]})
        )]
        print('.', end=' ')
    batch = mnist.train.next_batch(100)
    nn1.minimizer_tensor.run(feed_dict={nn1.input_tensor: batch[0], nn1.train_tensor: batch[1]})

acc_vec += [(
    accuracy.eval(feed_dict={nn1.input_tensor: mnist.train.images[:100], nn1.train_tensor: mnist.train.labels[:100]}),
    accuracy.eval(feed_dict={nn1.input_tensor: mnist.test.images[:100], nn1.train_tensor: mnist.test.labels[:100]})
)]
print('. 100%')

0% . 1% 2% 3% 4% 5% . 6% 7% 8% 9% 10% . 11% 12% 13% 14% 15% . 16% 17% 18% 19% 20% . 21% 22% 23% 24% 25% . 26% 27% 28% 29% 30% . 31% 32% 33% 34% 35% . 36% 37% 38% 39% 40% . 41% 42% 43% 44% 45% . 46% 47% 48% 49% 50% . 51% 52% 53% 54% 55% . 56% 57% 58% 59% 60% . 61% 62% 63% 64% 65% . 66% 67% 68% 69% 70% . 71% 72% 73% 74% 75% . 76% 77% 78% 79% 80% . 81% 82% 83% 84% 85% . 86% 87% 88% 89% 90% . 91% 92% 93% 94% 95% . 96% 97% 98% 99% . 100%


In [67]:
res = accuracy.eval(feed_dict={nn1.input_tensor: mnist.test.images[:100], nn1.train_tensor: mnist.test.labels[:100]})
res

0.89999998

In [68]:
res = accuracy.eval(feed_dict={nn1.input_tensor: mnist.test.images, nn1.train_tensor: mnist.test.labels})
res

0.88169998

In [69]:
m = tf.reduce_mean(nn1.lst_out, axis=0)
v = tf.reduce_max(tf.square(nn1.lst_out - m), axis=0)
m_max = tf.reduce_max(nn1.lst_out, axis=0)
m_min = tf.reduce_min(nn1.lst_out, axis=0)
mean, variance, weights_out, weight_max, weight_min, l0_layers = \
    session.run(
        (m, v, nn1.lst_out, m_max, m_min, nn1.l0_layers),
        feed_dict={nn1.input_tensor: mnist.test.images[:100], nn1.train_tensor: mnist.test.labels[:100]})

In [70]:
fig5_1 = p.figure(x_axis_label='Iterations', y_axis_label='Accuracy')

fig5_1.line(range(0, train_iters*100+1, 100*train_iters//20), [x[0] for x in acc_vec], line_color='blue', legend='Train')
fig5_1.square(range(0, train_iters*100+1, 100*train_iters//20), [x[0] for x in acc_vec], color='blue')
fig5_1.line(range(0, train_iters*100+1, 100*train_iters//20), [x[1] for x in acc_vec], line_color='red', legend='Test')
fig5_1.square(range(0, train_iters*100+1, 100*train_iters//20), [x[1] for x in acc_vec], color='red')

fig5_1.legend.location = 'top_left'
p.show(fig5_1)

In [71]:
fig5_2 = p.figure(x_range=[0,28*28], y_range=[0,10], x_axis_label='Input', y_axis_label='Output', title='Mean weights')
fig5_2.image([mean.reshape(28*28,10).T], 0, 0, 28*28, 10, palette='Magma256')

fig5_3 = p.figure(x_range=[0,28*28], y_range=[0,10], x_axis_label='Input', y_axis_label='Output', title='Weights variance')
fig5_3.image([variance.reshape(28*28,10).T], 0, 0, 28*28, 10, palette='Magma256')

p.show(bl.row(fig5_2, fig5_3))

In [72]:
fig5_2s = []
fig5_3s = []

for i in range(10):
    fig5_2_i = p.figure(x_range=[0,28], y_range=[28,0], title=f"Mean weights {i}")
    fig5_2_i.image([mean.reshape(28*28,10).T[i,:].reshape(28,28)[::-1,:]], 0, 28, 28, 28, palette='Magma256')
    fig5_2s += [fig5_2_i]
    
    fig5_3_i = p.figure(x_range=[0,28], y_range=[28,0], title=f"Weights variance {i}")
    fig5_3_i.image([variance.reshape(28*28,10).T[i,:].reshape(28,28)[::-1,:]], 0, 28, 28, 28, palette='Magma256')
    fig5_3s += [fig5_3_i]

p.show(bl.gridplot(fig5_2s, fig5_3s, plot_width=200, plot_height=200))

In [73]:
fig5_4s = []
fig5_idx = 0

for i in range(10):
    fig5_4_i = p.figure(x_range=[0,28], y_range=[28,0], title=f"Mean weights {i} at Test f{fig5_idx}")
    fig5_4_i.image([weights_out[fig5_idx].reshape(28*28,10).T[i,:].reshape(28,28)[::-1,:]], 0, 28, 28, 28, palette='Magma256')
    fig5_4s += [fig5_4_i]

p.show(bl.gridplot([fig5_4s], plot_width=200, plot_height=200))

In [37]:
fig5_5 = p.figure(x_range=[0,28], y_range=[28,0], title="Test f{fig5_idx}", plot_width=200, plot_height=200)
fig5_5.image([np.array(mnist.test.images[fig5_idx]).reshape(28,28)[::-1,:]], 0, 28, 28, 28)

p.show(fig5_5)

In [74]:
fig5_7 = p.figure(x_range=[0,nn1.config.ST.OUTPUT_SIZE], x_axis_label='Index', y_axis_label='Value', title='Mean weights')
fig5_7.vbar(range(nn1.config.ST.OUTPUT_SIZE), 1, weight_max, weight_min, color='red')
fig5_7.circle(range(nn1.config.ST.OUTPUT_SIZE), mean, color='blue', radius = 0.6)

p.show(fig5_7)

`1 layer-0 and 1 layer-1, div20 Selectrick`: Quite fast and fairly compact (compared to full class 1).
And relatively good results comparable to MLP. With shuffling and without results differ somewhat on first iterations
but converge on later.


#### Configuration 1

In [90]:
NNClassOneST_Cfg_1

{
   INPUT_SIZE: 784, 
   OUTPUT_SIZE: 10, 
   L0: {
      INPUT_SIZE: 784, 
      OUTPUT_SIZE: 10, 
      DEPTH: 3, 
      FACTOR: [1, 4, 1], 
      LAYER_SZ: [784 196  10], 
      WEIGHTS_SHAPES: [(784, 196), (196, 10)], 
      ACTS: [<function elu at 0x7ff56f586620>, <function identity at 0x7ff5702e4f28>], 
      NORM: [True, False], 
      BIAS: [0.1, 0.0], 
      WEIGHTS_SZ: [153664, 1960]
   }, 
   ST: {
      MEDIAL_SIZE: 28, 
      INPUT_SIZE: 5558, 
      OUTPUT_SIZE: 155624, 
      STDDEV: 0.1, 
      BIAS: 0.1, 
      WEIGHTSACT: <function softmax at 0x7ff56f17eb70>, 
      SHUFFLE: <bound method NNClassOneST_Cfg_1.st_shuffle of <class '__main__.NNClassOneST_Cfg_1'>>, 
      MAP: [0, 1, 2, 3, 4, 5, 6, 28, 29, 30, 31, 32, 33, 34, 56, 57, 58, 59, 60, 61, 62, 84, 85, 86, 87, 88, 89, 90, 112, 113, 114, 115, 116, 117, 118, 140, 141, 142, 143, 144, 145, 146, 168, 169, 170, 171, 172, 173, 174, 196, 197, 198, 199, 200, 201, 202, 224, 225, 226, 227, 228, 229, 230, 252, 253, 254, 255,

In [91]:
# Reset TF graph environment
try:
    del nn0
    del accuracy
    session.close()
    del session
except:
    pass

tf.reset_default_graph()
random.seed(1234)
np.random.seed(1234)
tf.set_random_seed(1234)

session = tf.InteractiveSession()

In [92]:
from tensorflow.examples.tutorials.mnist import input_data
mnist = input_data.read_data_sets('MNIST_data', one_hot=True)

Extracting MNIST_data/train-images-idx3-ubyte.gz
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz


In [95]:
def f_error_softmax(train, result):
    return tf.nn.softmax_cross_entropy_with_logits(labels = train, logits = result)

nn1 = ClassOneSTNN(NNClassOneST_Cfg_1)
nn1.setup_nn()
nn1.setup_error(f_error_softmax, tf.train.AdamOptimizer, [0.1])

correct_prediction = tf.equal(tf.argmax(nn1.l0_out,1), tf.argmax(nn1.train_tensor,1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))


/usr/local/lib/python3.6/dist-packages/tensorflow/python/ops/gradients_impl.py:93: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


In [96]:
tf.global_variables_initializer().run()

In [97]:
acc_vec = []

train_iters = 200

for i in range(train_iters):
    if i % (train_iters//100) == 0:
        print(f"{i//(train_iters//100)}%", end=' ')
    if i % (train_iters//20) == 0:
        acc_vec += [(
            accuracy.eval(feed_dict={nn1.input_tensor: mnist.train.images[:100], nn1.train_tensor: mnist.train.labels[:100], nn1.phase: 0}),
            accuracy.eval(feed_dict={nn1.input_tensor: mnist.test.images[:100], nn1.train_tensor: mnist.test.labels[:100], nn1.phase: 0})
        )]
        print('.', end=' ')
    batch = mnist.train.next_batch(100)
    nn1.minimizer_tensor.run(feed_dict={nn1.input_tensor: batch[0], nn1.train_tensor: batch[1], nn1.phase: 1})

acc_vec += [(
    accuracy.eval(feed_dict={nn1.input_tensor: mnist.train.images[:100], nn1.train_tensor: mnist.train.labels[:100], nn1.phase: 0}),
    accuracy.eval(feed_dict={nn1.input_tensor: mnist.test.images[:100], nn1.train_tensor: mnist.test.labels[:100], nn1.phase: 0})
)]
print('. 100%')

0% . 1% 2% 3% 4% 5% . 6% 7% 8% 9% 10% . 11% 12% 13% 14% 15% . 16% 17% 18% 19% 20% . 21% 22% 23% 24% 25% . 26% 27% 28% 29% 30% . 31% 32% 33% 34% 35% . 36% 37% 38% 39% 40% . 41% 42% 43% 44% 45% . 46% 47% 48% 49% 50% . 51% 52% 53% 54% 55% . 56% 57% 58% 59% 60% . 61% 62% 63% 64% 65% . 66% 67% 68% 69% 70% . 71% 72% 73% 74% 75% . 76% 77% 78% 79% 80% . 81% 82% 83% 84% 85% . 86% 87% 88% 89% 90% . 91% 92% 93% 94% 95% . 96% 97% 98% 99% . 100%


In [98]:
res = accuracy.eval(feed_dict={nn1.input_tensor: mnist.test.images[:100], nn1.train_tensor: mnist.test.labels[:100], nn1.phase: 0})
res

0.89999998

In [ ]:
# NOTE: this may crash due to memory limits
res = accuracy.eval(feed_dict={nn1.input_tensor: mnist.test.images, nn1.train_tensor: mnist.test.labels})
res

In [99]:
m = tf.reduce_mean(nn1.lst_out, axis=0)
v = tf.reduce_max(tf.square(nn1.lst_out - m), axis=0)
m_max = tf.reduce_max(nn1.lst_out, axis=0)
m_min = tf.reduce_min(nn1.lst_out, axis=0)
mean, variance, weights_out, weight_max, weight_min, l0_layers = \
    session.run(
        (m, v, nn1.lst_out, m_max, m_min, nn1.l0_layers),
        feed_dict={nn1.input_tensor: mnist.test.images[:100], nn1.train_tensor: mnist.test.labels[:100], nn1.phase: 0})

In [100]:
fig6_1 = p.figure(x_axis_label='Iterations', y_axis_label='Accuracy')

fig6_1.line(range(0, train_iters*100+1, 100*train_iters//20), [x[0] for x in acc_vec], line_color='blue', legend='Train')
fig6_1.square(range(0, train_iters*100+1, 100*train_iters//20), [x[0] for x in acc_vec], color='blue')
fig6_1.line(range(0, train_iters*100+1, 100*train_iters//20), [x[1] for x in acc_vec], line_color='red', legend='Test')
fig6_1.square(range(0, train_iters*100+1, 100*train_iters//20), [x[1] for x in acc_vec], color='red')

fig6_1.legend.location = 'top_left'
p.show(fig6_1)

/usr/local/lib/python3.6/dist-packages/bokeh/core/json_encoder.py:73: FutureWarning: pandas.tslib is deprecated and will be removed in a future version.
You can access Timestamp as pandas.Timestamp
  if pd and isinstance(obj, pd.tslib.Timestamp):


In [101]:
fig6_idx = 0
fig6_5 = p.figure(x_range=[0,28], y_range=[28,0], title="Test f{fig5_idx}", plot_width=200, plot_height=200)
fig6_5.image([np.array(mnist.test.images[fig6_idx]).reshape(28,28)[::-1,:]], 0, 28, 28, 28)

fig6_6 = p.figure(x_range=[0,28], y_range=[28,0], title="Test f{fig5_idx}", plot_width=200, plot_height=200)
fig6_6.image([l0_layers[1][0].reshape(14,14)[::-1,:]], 0, 28, 28, 28)

p.show(bl.row(fig6_5, fig6_6))

In [102]:
fig6_7 = p.figure(x_range=[0,nn1.config.ST.OUTPUT_SIZE], x_axis_label='Index', y_axis_label='Value', title='Mean weights')
fig6_7.vbar(range(nn1.config.ST.OUTPUT_SIZE), 1, weight_max, weight_min, color='red')
fig6_7.circle(range(nn1.config.ST.OUTPUT_SIZE), mean, color='blue', radius = 0.6)

p.show(fig6_7)

In [279]:
l0_layers[2][0]

array([-4254.7890625 ,   858.30206299, -1084.41760254,  -489.21557617,
        -856.24224854, -5000.88671875, -2972.99291992,  7559.27392578,
       -2672.51489258,   870.19775391], dtype=float32)

### Neural network configuration

In [21]:
random.seed(1234)
np.random.seed(1234)

class NNClassOne_Cfg_1(ReprStruct):
    
    INPUT_SIZE = np.prod(dataset_image_shape)
    OUTPUT_SIZE = 16*16
    
    class L0(ReprStruct): pass
    class L1(ReprStruct): pass
    
        
    L0.INPUT_SIZE = INPUT_SIZE
    L0.OUTPUT_SIZE = OUTPUT_SIZE
    L0.DEPTH = 4
    L0.FACTOR = 4
    L0.LAYER_SZ = nn_layer_sizes(L0.FACTOR, L0.INPUT_SIZE, L0.OUTPUT_SIZE, L0.DEPTH)
    L0.WEIGHTS_SHAPES = weight_matrices_shapes_for_layers(L0.LAYER_SZ)
    L0.ACTS = [tf.nn.sigmoid, tf.nn.sigmoid, tf.nn.sigmoid]
    
    L0.SPARSITY = [0.001, 0.003, 0.01]
    L0.WEIGHTS_INDICES = weights_sparse_indices(L0.WEIGHTS_SHAPES, L0.SPARSITY)
    L0.WEIGHTS_SZ = [len(w) for w in L0.WEIGHTS_INDICES]
    
    
    L1.INPUT_SIZE = INPUT_SIZE
    L1.OUTPUT_SIZE = sum(L0.WEIGHTS_SZ)
    L1.DEPTH = 4
    L1.FACTOR = 1./16
    L1.LAYER_SZ = nn_layer_sizes(L1.FACTOR, L1.INPUT_SIZE, L1.OUTPUT_SIZE, L1.DEPTH)
    L1.WEIGHTS_SHAPES = weight_matrices_shapes_for_layers(L1.LAYER_SZ)
    L1.ACTS = [tf.nn.sigmoid, tf.nn.sigmoid, tf.nn.sigmoid]



In [ ]:
NNClassOne_Cfg_1

### Running neural network

Restart TF.

In [ ]:
# Reset TF graph environment
try:
    del nn
    del accuracy
    session.close()
    del session
except:
    pass

tf.reset_default_graph()
random.seed(1234)
np.random.seed(1234)
tf.set_random_seed(1234)

session = tf.InteractiveSession()

In [ ]:
def f_error_l2(train, result):
    return tensorflow.losses.mean_squared_error(train, result)

nn = ClassOneNN(NNClassOne_Cfg_1)
nn.setup_nn()
nn.setup_error(f_error_l2, tf.train.GradientDescentOptimizer, [0.5])

accuracy = tf.sqrt(tf.reduce_mean(tf.squared_difference(nn.train_tensor, nn.l0_out)))

In [ ]:
tf.global_variables_initializer().run()

In [ ]:
rolling_idx = 0
batch = 50

for i in range(1000):
    nn.minimizer_tensor.run(feed_dict={
        nn.input_tensor: full_dataset_train[0][rolling_idx:rolling_idx+batch],
        nn.train_tensor: full_dataset_train[1][rolling_idx:rolling_idx+batch]})
    rolling_idx += batch
    if len(full_dataset_train[0]) <= rolling_idx:
        rolling_idx = rolling_idx % len(full_dataset_train[0])
    if i % 10 == 0:
        print(f"{i//10}%", end=' ')
print()

In [ ]:
run_metadata = tf.RunMetadata()
with open('timeline.ctf.json', 'w') as trace_file:

    session.run(nn.minimizer_tensor, feed_dict={
        nn.input_tensor: full_dataset_train[0][0:batch],
        nn.train_tensor: full_dataset_train[1][:batch]},
                options=tf.RunOptions(trace_level=tf.RunOptions.FULL_TRACE),
                run_metadata=run_metadata)

    trace = timeline.Timeline(step_stats=run_metadata.step_stats)
    trace_file.write(trace.generate_chrome_trace_format())


In [ ]:
res = accuracy.eval(feed_dict={nn.input_tensor: full_dataset_test[0][:batch], nn.train_tensor: full_dataset_test[1][:batch]})
res_train = accuracy.eval(feed_dict={nn.input_tensor: full_dataset_train[0][:batch], nn.train_tensor: full_dataset_train[1][:batch]})
output_res = nn.l0_out.eval(feed_dict={nn.input_tensor: full_dataset_test[0][:batch], nn.train_tensor: full_dataset_test[1][:batch]})
output_res_train = nn.l0_out.eval(feed_dict={nn.input_tensor: full_dataset_train[0][:batch], nn.train_tensor: full_dataset_train[1][:batch]})
print(res, res_train)

In [ ]:
fig4 = plt.figure()
ax_4_1 = fig4.add_subplot(2, 2, 1)
ax_4_2 = fig4.add_subplot(2, 2, 2)
ax_4_3 = fig4.add_subplot(2, 2, 3)

In [ ]:
SHOW_SET = 4
# USED_SET = (output_res, full_dataset_test)
USED_SET = (output_res_train, full_dataset_train)
ax_4_1.clear(); ax_4_2.clear(); ax_4_3.clear();
ax_4_1.imshow(USED_SET[1][0][SHOW_SET].reshape(64,64));
ax_4_2.imshow(USED_SET[1][1][SHOW_SET].reshape(16,16));
ax_4_3.imshow(USED_SET[0][SHOW_SET].reshape(16,16));

In [ ]:
print(max(output_res[0]), min(output_res[0]))


In [104]:
run_metadata = tf.RunMetadata()
with open('timeline.ctf.json', 'w') as trace_file:
    batch = mnist.train.next_batch(100)
    session.run(nn1.minimizer_tensor, feed_dict={nn1.input_tensor: batch[0], nn1.train_tensor: batch[1]},
                options=tf.RunOptions(trace_level=tf.RunOptions.FULL_TRACE),
                run_metadata=run_metadata)

    trace = timeline.Timeline(step_stats=run_metadata.step_stats)
    trace_file.write(trace.generate_chrome_trace_format())



Actually, no. I think we are not ready for Class One, at least with the resources we have. We will go for Class Two.

The structure is following:

```

W \
W - N1 \
W /     \ N0 <- I
W \     /
W - N1 /
W /

```

where `W` is a weight of level-0 network either with random sparse connections or fully-connected, `N1` is a small-sized fully-connected level-1 neural network, repeated over all `W`s, `N0` is a fully-connected level-2 neural network, taking image data `I` as input.